![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo P 2019 Consumo de Álcool

## Bibliotecas Utilizadas

In [5]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [4]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA>")

## Definição do peso e filtragem de respondentes do questionario

In [6]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2019.1<-pns2019v3 %>% filter(V0025A==1)
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(94114/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00582  0.27579  0.56358  1.03597  1.16822 63.29775 

## Criação de variáveis dos indicadores

In [7]:
#Desfechos - Indicadores

#P010P - Consumo de bebida alcoólica uma vez ou mais por semana
pns2019.1$P02801[which(is.na(pns2019.1$P02801))] <- 0
pns2019.1 <- pns2019.1 %>% filter(P02801!=9) %>% mutate(P010P = ifelse(P02801>=1, 1,2))
pns2019.1$P010P<-factor(pns2019.1$P010P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2019.1$P010P)

#P011P - Consumo regular de bebida alcoólica
pns2019.1$P02801[which(is.na(pns2019.1$P02801))] <- 0
pns2019.1 <- pns2019.1 %>% filter(P02801!=9) %>% mutate(P011P = ifelse(P02801>=5, 1,2))
pns2019.1$P011P<-factor(pns2019.1$P011P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2019.1$P011P)

#P012P - Consumo abusivo de álcool nos últimos 30 dias
pns2019.1$P03201[which(is.na(pns2019.1$P03201))] <- 0
pns2019.1 <- pns2019.1 %>% filter(P03201!=9) %>% mutate(P012P = ifelse(P03201==1, 1,2))
pns2019.1$P012P<-factor(pns2019.1$P012P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2019.1$P012P)

#P013P - Dirigir automóvel ou motocicleta logo depois de beber nos últimos 12 meses
pns2019.1$P03001[which(is.na(pns2019.1$P03001))] <- 0
pns2019.1 <- pns2019.1 %>% filter(P03001!=9|P03001>0) %>% mutate(P013P = ifelse(P03001==1, 1,2))
pns2019.1$P013P<-factor(pns2019.1$P013P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2019.1$P013P)




Sim   Nao 
21106 69740

Sim   Nao 
 2078 88768

Sim   Nao 
15032 75814

Sim   Nao 
 4045 86801

## Definições de abrangências

### Situação urbana ou rural

In [8]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2019.1$Sit_Urbano_Rural)

Urbano  Rural 
 69873  20973

### Sexo

In [9]:
#Sexo
pns2019.1 <- pns2019.1 %>% rename(Sexo=C006)
pns2019.1$Sexo<-factor(pns2019.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2019.1$Sexo)

Masculino  Feminino 
    42799     48047

### UF

In [10]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondonia","Acre","Amazonas","Roraima","Para","Amapa","Tocantins","Maranhao","Piaui","Ceara",
                                        "Rio Grande do Norte","Paraiba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espirito Santo","Rio de Janeiro","Sao Paulo",
                                        "Parana","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goias","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondonia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Para               Amapa           Tocantins            Maranhao 
               3853                1554                1922                5080 
              Piaui               Ceara Rio Grande do Norte             Paraiba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espirito Santo      Rio de Janeiro           Sao Paulo 
               5209                3541                4966                6114 
             Parana      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goias    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [11]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `1 Norte` = c("Rondonia","Acre","Amazonas","Roraima","Para", "Amapa","Tocantins"),
                                          `2 Nordeste` = c("Maranhao", "Piaui", "Ceara", "Rio Grande do Norte", "Paraiba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `3 Sudeste` = c("Minas Gerais", "Espirito Santo","Rio de Janeiro", "Sao Paulo"), 
                                          `4 Sul` = c("Parana", "Santa Catarina", "Rio Grande do Sul"),
                                          `5 Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goias", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

1 Norte     2 Nordeste      3 Sudeste          4 Sul 5 Centro-Oeste 
         17602          31544          19830          11472          10398

### Capital

In [12]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondonia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco `= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Boa Vista`= "Roraima",
                                        `Belem` = "Para" ,
                                        `Macapa`= "Amapa",
                                        `Palmas` = "Tocantins",
                                        `Sao Luis` = "Maranhao",
                                        `Teresina`= "Piaui" ,
                                        `Fortaleza`= "Ceara",
                                        `Natal`= "Rio Grande do Norte",
                                        `Joao Pessoa`= "Paraiba",
                                        `Recife`= "Pernambuco",
                                        `Maceio`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitoria`= "Espirito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `Sao Paulo`= "Sao Paulo",
                                        `Curitiba`= "Parana",
                                        `Florianopolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiaba`= "Mato Grosso",
                                        `Goiania` = "Goias",
                                        `Brasilia`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho    Rio Branco          Manaus      Boa Vista          Belem 
          2176           2380           3479           2238           3853 
        Macapa         Palmas       Sao Luis       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    Joao Pessoa         Recife         Maceio        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitoria Rio de Janeiro      Sao Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianopolis   Porto Alegre   Campo Grande         Cuiaba 
          3967           3738           3767           2863           2468 
       Goiania       Brasilia 
          2702           2365

### Faixa Etária

In [13]:
#Faixas Etárias
pns2019.1 <-  pns2019.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos    60 a 74 anos 75 anos ou mais 
          15394           26754           23655           16767            5961 
           NA's 
           2315

### Raça

In [14]:
#Raça
pns2019.1 <- pns2019.1 %>% filter(C009!=3|C009!=5|C009!=9)%>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2 , 2, 3)))
pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2019.1$Raca)

Branca  Preta  Parda 
 33133  10345  47368

### Renda per capita

In [15]:
#Rendimento domiciliar per capita

pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4,5)))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Ate 1/2 SM","1/2 ate 1 SM","1 ate 2 SM",
                                                                                   "2 ate 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Ate 1/2 SM 1/2 ate 1 SM   1 ate 2 SM   2 ate 3 SM Mais de 3 SM 
       23697        26406        22466         7612        10665

### Escolaridade

In [16]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Sem instrucao e fundamental incompleto","Fundamental completo e medio incompleto",
                                           "Medio completo e superior incompleto","Superior completo"))
summary(pns2019.1$gescol)

Sem instrucao e fundamental incompleto Fundamental completo e medio incompleto 
                                  36276                                   13520 
   Medio completo e superior incompleto                       Superior completo 
                                  27433                                   13617

## Criando indicadores

### Filtrando base de indicadores

In [17]:
#Selecionando variáveis para cálculo de indicadores no survey_ALTERAR
pns2019Psurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "P010P","P011P","P012P", "P013P",
                                     "C008","V0031","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita","gescol", "Capital")
summary(pns2019Psurvey)

     V0024            UPA_PNS          peso_morador_selec P010P      
 Min.   :1110011   Min.   :110000016   Min.   : 0.00582   Sim:21106  
 1st Qu.:2210011   1st Qu.:220001391   1st Qu.: 0.27579   Nao:69740  
 Median :2853020   Median :280039950   Median : 0.56358              
 Mean   :2998072   Mean   :296695855   Mean   : 1.03597              
 3rd Qu.:3553013   3rd Qu.:350588998   3rd Qu.: 1.16822              
 Max.   :5310220   Max.   :530051067   Max.   :63.29775              
                                                                     
 P011P       P012P       P013P            C008            V0031      
 Sim: 2078   Sim:15032   Sim: 4045   Min.   : 15.00   Min.   :1.000  
 Nao:88768   Nao:75814   Nao:86801   1st Qu.: 32.00   1st Qu.:1.000  
                                     Median : 45.00   Median :2.000  
                                     Mean   : 46.39   Mean   :2.605  
                                     3rd Qu.: 60.00   3rd Qu.:4.000  
                    

### Exporta tabela filtrada

In [66]:
#Salvando csv para cálculo de indicadores no survey_ALTERAR
path <- "<coloque aqui o caminho onde deseja salvar a base filtrada>"
write.csv(pns2019Psurvey, file.path(path, "pns2019Psurvey.csv"))

### Cria plano amostral complexo

In [18]:
#survey design
desPNSP=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2019Psurvey)
desPNSP18=subset(desPNSP, C008>=18)
desPNSPC=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2019Psurvey)
desPNSPC18=subset(desPNSPC, C008>=18 & V0031==1)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [53]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [54]:
#Cálculo dos indicadores usando o pacote survey - alterar
ListaIndicadores = c(~P010P,~P011P,~P012P,~P013P)
ListaIndicadoresTexto = c("P010P","P011P","P012P","P013P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTexto = c("Sexo","raca","rend_per_capita","fx_idade_18","urb_rur","uf","regiao","capital","gescol")
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [55]:
i <- 0
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
              if (ListaDominiosTexto[j]=="capital"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSPC18 , svymean,vartype=c("ci","cv"))
               }else{
                    dataframe_indicador<-svyby( indicador , dominio , desPNSP18 , svymean,vartype=c("ci","cv"))
               }
        
               dataframe_indicador<-data.frame(dataframe_indicador)
              
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}

#### Criando a tabela pela abrangência total

In [56]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [57]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        dataframe_indicador_N <- data.frame()
        if(total == 'Capital'){
            dataframe_indicador <- svymean(indicador,desPNSPC18)
        }else{
            dataframe_indicador <- svymean(indicador,desPNSP18)
        }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))

        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        
        dataframe_indicador <- dataframe_indicador %>% 
                                 slice(1)
        colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','cvS')
        dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador$abr_tipo <- "total"
        dataframe_indicador$abr_nome <- total
        dataframe_indicador$Ano <- Ano 
        dataframe_indicador <- dataframe_indicador %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador",'Sim','LowerS','UpperS','cvS')
       
        matriz_totais <-rbind(matriz_totais,dataframe_indicador)
        
    }
}

#### Unindo tabela de indicadores e de totais

In [58]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Exportando tabela de indicadores

In [71]:
write.table(matrizIndicadores,file="<coloque aqui o caminho para exportação da matriz de indicadores>",sep = ";",dec = ",",row.names = FALSE)